# SHAP feature selection #
## Code to select feature with combination of LightGBM and SHAP ##

## Parameters cell ##

Parameters are overiddent by papermill when run inside DVC stages



In [1]:
n_folds = 5 # this sets global setting of which how many bootstraps to use
n_hold_out = 1
repeats = 10
importance_type = "split"

life_history = ["lifespan", "mass_kg", "mtGC", "metabolic_rate", "temperature", "gestation_days"]
debug_local = True #to use local version

In [2]:
from pathlib import Path
import sys
import inspect

#lgb_params["importance_type"] = importance_type

local = (Path("..") / "yspecies").resolve()
if debug_local and local.exists():
  sys.path.insert(0, Path("..").as_posix())
  #sys.path.insert(0, local.as_posix())
  print("extending pathes with local yspecies")
  print(sys.path)
  %load_ext autoreload
  %autoreload 2

extending pathes with local yspecies
['..', '/data/sources/yspecies/notebooks', '/opt/miniconda3/envs/yspecies/lib/python38.zip', '/opt/miniconda3/envs/yspecies/lib/python3.8', '/opt/miniconda3/envs/yspecies/lib/python3.8/lib-dynload', '', '/opt/miniconda3/envs/yspecies/lib/python3.8/site-packages', '/opt/miniconda3/envs/yspecies/lib/python3.8/site-packages/IPython/extensions', '/home/antonkulaga/.ipython']


In [3]:
from dataclasses import dataclass, replace
import numpy as np
import pandas as pd
from sklearn.pipeline import Pipeline
import seaborn as sns
import matplotlib.pyplot as plt

In [4]:
from typing import *
from yspecies.dataset import *
from yspecies.utils import *
from yspecies.workflow import TupleWith, Repeat, Collect
from yspecies.config import *
from yspecies.preprocess import FeatureSelection, DataExtractor
from yspecies.partition import DataPartitioner, PartitionParameters
from yspecies.models import Metrics
from yspecies.selection import ShapSelector
from yspecies.results import FeatureSummary

In [5]:
import optuna
from optuna import Study, Trial
from optuna import multi_objective
from optuna.multi_objective import trial
from optuna.multi_objective.study import MultiObjectiveStudy
from yspecies.tuning import MultiObjectiveResults

In [6]:
#settings
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.float_format', lambda x: '%.3f' % x)
import pprint
pp = pprint.PrettyPrinter(indent=4)

#charts settings
import matplotlib.pyplot as plt
from IPython.display import set_matplotlib_formats
%matplotlib auto
plt.ioff()
set_matplotlib_formats('svg')

Using matplotlib backend: TkAgg


### Loading data ###
Let's load data from species/genes/expressions selected by select_samples.py notebook

In [7]:
from pathlib import Path
locations: Locations = Locations("./") if Path("./data").exists() else Locations("../")

## Setting up Features to select ##

In [8]:
default_selection = FeatureSelection(
    samples = ["tissue","species"], #samples metadata to include
    species =  [], #species metadata other then Y label to include
    exclude_from_training = ["species"],  #exclude some fields from LightGBM training
    to_predict = "lifespan", #column to predict
    categorical = ["tissue"],
    select_by = "shap",
    importance_type =  importance_type,
    feature_perturbation = "tree_path_dependent"
)
default_selection

FeatureSelection(samples=['tissue', 'species'], species=[], genes=None, to_predict='lifespan', categorical=['tissue'], exclude_from_training=['species'], genes_meta=None, select_by='shap', importance_type='split', feature_perturbation='tree_path_dependent', not_validated_species=[])

In [9]:
loader = DataLoader(locations, default_selection)
selections = loader.load_life_history()
selections["lifespan"][0]

<table border='2'><caption>lifespan<caption><tr><th>expressions</th><th>genes</th><th>species</th><th>samples</th><th>Genes Metadata</th><th>Species Metadata</th></tr><tr><td>(408, 12323)</td><td>(12323, 37)</td><td>38</td><td>408</td><td>(12323, 2)</td><td>(38, 18)</td></tr></table>

## Setting up SHAP selection pipeline ##

In [10]:
from yspecies.helpers import PipelineFactory
factory = PipelineFactory(locations,repeats, n_folds, n_hold_out)


In [11]:
pipelines = {trait:factory.make_repeated_shap_pipeline(trait) for trait in life_history}
pipelines.keys()

loading (if exists) study from sqlite:////data/sources/yspecies/notebooks/../data/interim/optimization/lifespan.sqlite


create_study is experimental (supported from v1.4.0). The interface can change in the future.
NSGAIIMultiObjectiveSampler is experimental (supported from v1.5.0). The interface can change in the future.
RandomMultiObjectiveSampler is experimental (supported from v1.4.0). The interface can change in the future.
[I 2020-09-19 15:57:51,396] Using an existing study with name 'lifespan_r2_huber_kendall' instead of creating a new one.
MultiObjectiveStudy is experimental (supported from v1.4.0). The interface can change in the future.
FrozenMultiObjectiveTrial is experimental (supported from v1.4.0). The interface can change in the future.


loading (if exists) study from sqlite:////data/sources/yspecies/notebooks/../data/interim/optimization/mass_kg.sqlite


[I 2020-09-19 15:57:52,897] Using an existing study with name 'mass_kg_r2_huber_kendall' instead of creating a new one.


loading (if exists) study from sqlite:////data/sources/yspecies/notebooks/../data/interim/optimization/mtGC.sqlite


...

loading (if exists) study from sqlite:////data/sources/yspecies/notebooks/../data/interim/optimization/temperature.sqlite


[I 2020-09-19 15:57:54,552] Using an existing study with name 'temperature_r2_huber_kendall' instead of creating a new one.


loading (if exists) study from sqlite:////data/sources/yspecies/notebooks/../data/interim/optimization/gestation_days.sqlite


[I 2020-09-19 15:57:54,882] Using an existing study with name 'gestation_days_r2_huber_kendall' instead of creating a new one.


dict_keys(['lifespan', 'mass_kg', 'mtGC', 'metabolic_rate', 'temperature', 'gestation_days'])

# First stage selection (shap ) #

In [12]:
stage_one = {}

In [13]:
def run_stage_one(trait: str):
    result = pipelines[trait].fit_transform(selections[trait])
    stage_one[trait] = result #ugly mutation of stage_one dicionary
    return result

## Lifespan ##

In [ ]:
stage_one_lifespan = run_stage_one("lifespan")
stage_one_lifespan.selected

2020-09-19 15:57:55.906 | INFO     | yspecies.selection:fit:135 - ===== fitting models with seed 0 =====
2020-09-19 15:57:55.906 | INFO     | yspecies.selection:fit:136 - PARAMETERS:
{'bagging_fraction': 0.9223944053685549, 'boosting_type': 'gbdt', 'drop_rate': 0.29847846764282016, 'feature_fraction': 0.30501714460224083, 'lambda_l1': 0.21894440516534, 'lambda_l2': 1.3848191603958375, 'learning_rate': 0.08210966706622723, 'max_depth': 3, 'max_leaves': 17, 'min_data_in_leaf': 8, 'objective': 'regression', 'metrics': ['l1', 'l2', 'huber'], 'verbose': -1, 'early_stopping_round': 10}
2020-09-19 15:57:55.933 | INFO     | yspecies.selection:fit:139 - SEED: 0 | FOLD: 0 | VALIDATION_SPECIES: ['Gorilla_gorilla', 'Pan_paniscus']
Found `early_stopping_round` in params. Will use it instead of argument


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[136]	valid_0's l1: 9.45903	valid_0's l2: 229.227	valid_0's huber: 8.15653


2020-09-19 15:57:57.788 | INFO     | yspecies.selection:fit:139 - SEED: 0 | FOLD: 1 | VALIDATION_SPECIES: ['Heterocephalus_glaber', 'Capra_hircus']


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[126]	valid_0's l1: 4.44458	valid_0's l2: 75.2891	valid_0's huber: 3.67282


2020-09-19 15:57:59.722 | INFO     | yspecies.selection:fit:139 - SEED: 0 | FOLD: 2 | VALIDATION_SPECIES: ['Bos_taurus', 'Otolemur_garnettii']


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[108]	valid_0's l1: 3.84279	valid_0's l2: 54.7746	valid_0's huber: 3.13819


2020-09-19 15:58:01.695 | INFO     | yspecies.selection:fit:139 - SEED: 0 | FOLD: 3 | VALIDATION_SPECIES: ['Macaca_nemestrina', 'Microcebus_murinus']


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[101]	valid_0's l1: 3.48671	valid_0's l2: 64.2862	valid_0's huber: 2.79989


### saving partitions info  ###

In [52]:
stage_one_lifespan.write(locations.interim.stage_one / "partitions", "lifespan_stage_one")

PosixPath('../data/interim/stage_1/partitions')

### Mass_kg ###

In [17]:
stage_one_mass = run_stage_one("mass_kg")
stage_one_mass.selected

2020-09-13 01:00:41.495 | INFO     | yspecies.selection:fit:79 - ===== fitting models with seed 0 =====
2020-09-13 01:00:41.496 | INFO     | yspecies.selection:fit:80 - PARAMETERS:
{'bagging_fraction': 0.49885668399953875, 'boosting_type': 'dart', 'drop_rate': 0.2372958868935867, 'feature_fraction': 0.49141007534802034, 'lambda_l1': 0.656412473127467, 'lambda_l2': 1.9535470163293591, 'learning_rate': 0.08702343727058373, 'max_depth': 3, 'max_leaves': 21, 'min_data_in_leaf': 8, 'objective': 'regression', 'metrics': ['l1', 'l2', 'huber'], 'verbose': -1, 'early_stopping_round': 10}
2020-09-13 01:00:41.516 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 0 | VALIDATION_SPECIES: ['Monodelphis_domestica', 'Aotus_nancymaae']
Found `early_stopping_round` in params. Will use it instead of argument
Early stopping is not available in dart mode


[250]	valid_0's l1: 13.3421	valid_0's l2: 445.825	valid_0's huber: 11.6282


2020-09-13 01:00:43.764 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 1 | VALIDATION_SPECIES: ['Sus_scrofa', 'Oryctolagus_cuniculus']


[250]	valid_0's l1: 32.5505	valid_0's l2: 2527.47	valid_0's huber: 28.9213


2020-09-13 01:00:46.139 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 2 | VALIDATION_SPECIES: ['Mesocricetus_auratus', 'Cavia_porcellus']


...

[250]	valid_0's l1: 5.21492	valid_0's l2: 86.4547	valid_0's huber: 4.34632


2020-09-13 01:05:49.286 | INFO     | yspecies.selection:fit:83 - SEED: 9 | FOLD: 3 | VALIDATION_SPECIES: ['Meriones_unguiculatus', 'Homo_sapiens']


[250]	valid_0's l1: 24.6386	valid_0's l2: 1476.01	valid_0's huber: 21.7903


2020-09-13 01:06:14.572 | INFO     | yspecies.selection:transform:227 - Metrics: 
Metrics(R2=0.8091649123643789, MAE=15.399116505148402, MSE=770.8173285998719, huber=13.492648050140154)


symbol  repeats  mean_shap  mean_kendall_tau  shap_0  \
ENSG00000144214     LYG1    7.000     10.429             0.408   6.250   
ENSG00000124172  ATP5F1E    6.000     20.500            -0.299     nan   
ENSG00000054277     OPN3    5.000     54.900             0.150  34.250   
ENSG00000066923    STAG3    5.000     26.450             0.154  38.750   
ENSG00000126062  TMEM115    5.000     10.750             0.005   7.000   
ENSG00000010219    DYRK4    4.000     21.188             0.212  23.000   
ENSG00000107020   PLGRKT    4.000     13.000             0.015  10.250   
ENSG00000270647    TAF15    4.000     11.750             0.043     nan   
ENSG00000152214     RIT2    4.000      2.875             0.065   2.750   
ENSG00000164304    CAGE1    3.000     15.000            -0.191  19.250   
ENSG00000204498  NFKBIL1    3.000      7.083            -0.193   8.500   
ENSG00000102265    TIMP1    3.000      3.417             0.031   2.250   
ENSG00000117151     CTBS    2.000     21.500            -0.268     nan   
ENSG00000108384   RAD51C    2.000      8.750             0.173   8.750   
ENSG00000101104  PABPC1L    2.000      1.875             0.308     nan   
ENSG00000109061     MYH1    1.000     33.000             0.070     nan   
ENSG00000127952   STYXL1    1.000     15.250             0.304     nan   
ENSG00000138430     OLA1    1.000     15.250             0.172     nan   
ENSG00000179532    DNHD1    1.000     14.500             0.299     nan   
ENSG00000213719    CLIC1    1.000     12.500            -0.091     nan   
ENSG00000160796   NBEAL2    1.000     12.250             0.071     nan   
ENSG00000175806     MSRA    1.000     10.750            -0.073     nan   
ENSG00000162438     CTRC    1.000     10.500             0.085     nan   
ENSG00000155849    ELMO1    1.000      8.250             0.190     nan   
ENSG00000092529    CAPN3    1.000      4.500             0.166     nan   
ENSG00000105397     TYK2    1.000      4.250             0.282     nan   
ENSG00000101842    VSIG1    1.000      4.000             0.460     nan   
ENSG00000164010    ERMAP    1.000      3.750             0.387     nan   
ENSG00000162949   CAPN13    1.000      3.500            -0.280   3.500   
ENSG00000136247   ZDHHC4    1.000      3.250            -0.022     nan   
ENSG00000182095   TNRC18    1.000      2.750             0.290     nan   
ENSG00000105379     ETFB    1.000      2.000             0.185   2.000   
ENSG00000144488    ESPNL    1.000      2.000             0.142   2.000   
ENSG00000231925    TAPBP    1.000      2.000             0.026     nan   
ENSG00000169857     AVEN    1.000      1.750            -0.157     nan   
ENSG00000171960     PPIH    1.000      1.750            -0.299     nan   
ENSG00000133256    PDE6B    1.000      1.500             0.281     nan   
ENSG00000118363    SPCS2    1.000      1.000             0.343   1.000   
ENSG00000182853     VMO1    1.000      1.000             0.313     nan   
ENSG00000103005     USB1    1.000      1.000            -0.500     nan   

                 kendall_tau_0  shap_1  kendall_tau_1  shap_2  kendall_tau_2  \
ENSG00000144214          0.413  17.750          0.406  11.000          0.319   
ENSG00000124172            nan     nan            nan   2.250         -0.276   
ENSG00000054277          0.164     nan            nan  66.750          0.267   
ENSG00000066923          0.222     nan            nan  11.500          0.147   
ENSG00000126062          0.014   8.250         -0.090     nan            nan   
ENSG00000010219          0.245     nan            nan     nan            nan   
ENSG00000107020         -0.035  12.500          0.053     nan            nan   
ENSG00000270647            nan  13.250          0.023  11.250          0.005   
ENSG00000152214          0.089   2.250          0.080     nan            nan   
ENSG00000164304         -0.215   3.250         -0.214     nan            nan   
ENSG00000204498         -0.236     nan            nan     nan            nan   
ENSG00000102265        

### MtGC ###

In [18]:
stage_one_mtGC = run_stage_one("mtGC")
stage_one_mtGC.selected

2020-09-13 01:06:14.762 | INFO     | yspecies.selection:fit:79 - ===== fitting models with seed 0 =====
2020-09-13 01:06:14.763 | INFO     | yspecies.selection:fit:80 - PARAMETERS:
{'bagging_fraction': 0.4882827581871194, 'boosting_type': 'gbdt', 'drop_rate': 0.16290376621758335, 'feature_fraction': 0.3059934876406196, 'lambda_l1': 0.017007142345511594, 'lambda_l2': 0.568546479848152, 'learning_rate': 0.08231879540454069, 'max_depth': 7, 'max_leaves': 24, 'min_data_in_leaf': 8, 'objective': 'regression', 'metrics': ['l1', 'l2', 'huber'], 'verbose': -1, 'early_stopping_round': 10}
2020-09-13 01:06:14.791 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 0 | VALIDATION_SPECIES: ['Callithrix_jacchus', 'Sus_scrofa']
Found `early_stopping_round` in params. Will use it instead of argument


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[104]	valid_0's l1: 0.478724	valid_0's l2: 0.473509	valid_0's huber: 0.201354


2020-09-13 01:06:17.862 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 1 | VALIDATION_SPECIES: ['Rattus_norvegicus', 'Gorilla_gorilla']


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[39]	valid_0's l1: 1.02058	valid_0's l2: 1.47366	valid_0's huber: 0.588529


2020-09-13 01:06:19.559 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 2 | VALIDATION_SPECIES: ['Macaca_mulatta', 'Equus_caballus']


...

Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[79]	valid_0's l1: 0.587505	valid_0's l2: 0.909156	valid_0's huber: 0.320914


2020-09-13 01:10:57.441 | INFO     | yspecies.selection:fit:83 - SEED: 9 | FOLD: 3 | VALIDATION_SPECIES: ['Mesocricetus_auratus', 'Cavia_porcellus']


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[41]	valid_0's l1: 0.973238	valid_0's l2: 1.77864	valid_0's huber: 0.577021


2020-09-13 01:11:10.142 | INFO     | yspecies.selection:transform:227 - Metrics: 
Metrics(R2=0.771141896946768, MAE=0.8484695237196214, MSE=1.4643304061387927, huber=0.4901653261780517)


symbol  repeats  mean_shap  mean_kendall_tau  shap_0  \
ENSG00000171121    KCNMB3   10.000     10.025             0.641  10.250   
ENSG00000122034     GTF3A   10.000      9.650             0.632  10.750   
ENSG00000144451    SPAG16   10.000      7.200             0.390   6.250   
ENSG00000196419     XRCC6    8.000     11.375             0.637   8.750   
ENSG00000167515  TRAPPC2L    8.000      4.031            -0.514   4.250   
ENSG00000163528    CHCHD4    6.000      5.333             0.402     nan   
ENSG00000167272      POP5    6.000      5.292            -0.381     nan   
ENSG00000122952     ZWINT    6.000      3.292            -0.663   3.000   
ENSG00000069869     NEDD4    6.000      2.542             0.010   4.250   
ENSG00000168300    PCMTD1    5.000      7.900             0.149   6.250   
ENSG00000006282   SPATA20    5.000      6.750             0.692     nan   
ENSG00000154328     NEIL2    5.000      6.500             0.652     nan   
ENSG00000188747     NOXA1    5.000      6.250             0.623   6.750   
ENSG00000178982     EIF3K    5.000      5.750             0.253   9.500   
ENSG00000176105      YES1    5.000      4.750             0.204   4.250   
ENSG00000171747    LGALS4    5.000      4.600            -0.664     nan   
ENSG00000164304     CAGE1    5.000      4.500            -0.695     nan   
ENSG00000156384      SFR1    5.000      4.150            -0.670   5.250   
ENSG00000055950    MRPL43    5.000      3.450             0.574   3.250   
ENSG00000129187      DCTD    5.000      2.750             0.678   3.000   
ENSG00000048140   TSPAN17    5.000      2.700            -0.414     nan   
ENSG00000170835       CEL    5.000      2.400             0.638     nan   
ENSG00000211454     AKR7L    4.000      4.688            -0.375     nan   
ENSG00000101190     TCFL5    4.000      4.250             0.554     nan   
ENSG00000177143     CETN1    4.000      3.562            -0.462     nan   
ENSG00000138678     GPAT3    4.000      3.125             0.070   3.750   
ENSG00000154582      ELOC    4.000      2.812            -0.482     nan   
ENSG00000167863    ATP5PD    4.000      2.750            -0.614   2.250   
ENSG00000023191      RNH1    4.000      2.188            -0.520     nan   
ENSG00000164362      TERT    3.000      5.917            -0.447   7.000   
ENSG00000092529     CAPN3    3.000      3.917             0.458   4.000   
ENSG00000101928    MOSPD1    3.000      3.750            -0.336     nan   
ENSG00000151006    PRSS53    3.000      3.000             0.622   1.250   
ENSG00000065548    ZC3H15    3.000      2.500             0.275     nan   
ENSG00000100908      EMC9    3.000      2.333            -0.606     nan   
ENSG00000278845    MRPL45    3.000      2.333            -0.645   2.750   
ENSG00000102699     PARP4    3.000      2.250             0.580     nan   
ENSG00000160447      PKN3    3.000      1.917             0.561     nan   
ENSG00000181704     YIPF6    3.000      1.750             0.300   1.500   
ENSG00000135452   TSPAN31    3.000      1.667             0.607   1.250   
ENSG00000134308     YWHAQ    3.000      1.667             0.452   1.750   
ENSG00000269058     CALR3    2.000      3.750            -0.474     nan   
ENSG00000168393     DTYMK    2.000      3.750            -0.619     nan   
ENSG00000157778     PSMG3    2.000      3.375             0.621     nan   
ENSG00000204954  C12orf73    2.000      3.125            -0.668     nan   
ENSG00000105672      ETV2    2.000      3.000             0.633   2.000   
ENSG00000242866      STRC    2.000      2.500             0.516     nan   
ENSG00000197629     MPEG1    2.000      2.375            -0.528     nan   
ENSG00000163584   RPL22L1    2.000      2.375            -0.626   1.750   
ENSG00000120594    PLXDC2    2.000      2.250             0.380     nan   
ENSG00000164010     ERMAP    2.000      2.000             0.479     nan   
ENSG00000182774     RPS17    2.000      2.000            -0.393     nan   
ENSG00000120992    LYPLA1    2.000      2.00

### Metabolism ###

In [19]:
stage_one_metabolic_rate = run_stage_one("metabolic_rate")
stage_one_metabolic_rate.selected

2020-09-13 01:11:10.322 | INFO     | yspecies.selection:fit:79 - ===== fitting models with seed 0 =====
2020-09-13 01:11:10.323 | INFO     | yspecies.selection:fit:80 - PARAMETERS:
{'bagging_fraction': 0.7949279232062532, 'boosting_type': 'dart', 'drop_rate': 0.19407161947050122, 'feature_fraction': 0.8486129005166576, 'lambda_l1': 2.9464767054398204, 'lambda_l2': 0.817423041659147, 'learning_rate': 0.08579903520990408, 'max_depth': 7, 'max_leaves': 15, 'min_data_in_leaf': 8, 'objective': 'regression', 'metrics': ['l1', 'l2', 'huber'], 'verbose': -1, 'early_stopping_round': 10}
2020-09-13 01:11:10.341 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 0 | VALIDATION_SPECIES: ['Monodelphis_domestica', 'Cavia_porcellus']
Found `early_stopping_round` in params. Will use it instead of argument
Early stopping is not available in dart mode


[250]	valid_0's l1: 12.9298	valid_0's l2: 299.517	valid_0's huber: 11.2671


2020-09-13 01:11:14.353 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 1 | VALIDATION_SPECIES: ['Sus_scrofa', 'Phascolarctos_cinereus']


[250]	valid_0's l1: 23.1846	valid_0's l2: 1147.18	valid_0's huber: 20.484


2020-09-13 01:11:20.434 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 2 | VALIDATION_SPECIES: ['Meriones_unguiculatus', 'Rattus_norvegicus']


...

[250]	valid_0's l1: 5.03709	valid_0's l2: 48.1837	valid_0's huber: 4.14782


2020-09-13 01:17:27.549 | INFO     | yspecies.selection:fit:83 - SEED: 9 | FOLD: 3 | VALIDATION_SPECIES: ['Homo_sapiens', 'Otolemur_garnettii']


[250]	valid_0's l1: 31.8386	valid_0's l2: 2012.26	valid_0's huber: 28.2706


2020-09-13 01:17:56.065 | INFO     | yspecies.selection:transform:227 - Metrics: 
Metrics(R2=0.7532232291971745, MAE=16.342121156276164, MSE=788.80540000597, huber=14.340174998612655)


symbol  repeats  mean_shap  mean_kendall_tau  shap_0  \
ENSG00000124172   ATP5F1E    6.000     27.708            -0.252  24.250   
ENSG00000270647     TAF15    6.000     23.583            -0.107     nan   
ENSG00000107020    PLGRKT    5.000     29.850             0.011  21.250   
ENSG00000054277      OPN3    4.000     39.438             0.092   2.000   
ENSG00000171747    LGALS4    4.000      6.625            -0.639  10.000   
ENSG00000175806      MSRA    3.000     17.167            -0.036  26.000   
ENSG00000127952    STYXL1    3.000      9.750             0.291     nan   
ENSG00000134825   TMEM258    3.000      5.500             0.581   9.750   
ENSG00000156467     UQCRB    3.000      3.000            -0.419   3.250   
ENSG00000198931      APRT    3.000      2.583             0.480   1.750   
ENSG00000164304     CAGE1    2.000     32.125            -0.225  29.500   
ENSG00000117151      CTBS    2.000     23.625            -0.090  21.750   
ENSG00000102901     CENPT    2.000     21.875             0.322     nan   
ENSG00000103150     MLYCD    2.000      8.875            -0.228     nan   
ENSG00000189043    NDUFA4    2.000      5.000            -0.318     nan   
ENSG00000164182   NDUFAF2    2.000      4.000            -0.588     nan   
ENSG00000101546      RBFA    2.000      3.875             0.423     nan   
ENSG00000183625      CCR3    2.000      3.500             0.282     nan   
ENSG00000103005      USB1    2.000      3.250             0.435     nan   
ENSG00000160446   ZDHHC12    2.000      3.250             0.140     nan   
ENSG00000198663   C6orf89    2.000      2.125            -0.463     nan   
ENSG00000182853      VMO1    2.000      1.750             0.349     nan   
ENSG00000077713  SLC25A43    2.000      1.625             0.321     nan   
ENSG00000108556     CHRNE    2.000      1.500             0.605   1.250   
ENSG00000105617     LENG1    1.000     34.000             0.023     nan   
ENSG00000278023      RDM1    1.000     19.750            -0.352     nan   
ENSG00000213719     CLIC1    1.000     18.250            -0.142     nan   
ENSG00000144214      LYG1    1.000     15.000             0.450     nan   
ENSG00000278845    MRPL45    1.000     14.000            -0.217     nan   
ENSG00000136247    ZDHHC4    1.000     13.500            -0.047     nan   
ENSG00000169857      AVEN    1.000     11.500            -0.170     nan   
ENSG00000065457     ADAT1    1.000     11.250             0.200     nan   
ENSG00000137411     VARS2    1.000     11.250             0.009     nan   
ENSG00000162814   SPATA17    1.000     11.000            -0.323     nan   
ENSG00000161055   SCGB3A1    1.000      9.000             0.147     nan   
ENSG00000170542  SERPINB9    1.000      6.500             0.688     nan   
ENSG00000204498   NFKBIL1    1.000      5.500            -0.344     nan   
ENSG00000197622  CDC42SE1    1.000      5.250            -0.016     nan   
ENSG00000160796    NBEAL2    1.000      5.000            -0.104     nan   
ENSG00000108384    RAD51C    1.000      4.750             0.391     nan   
ENSG00000174695  TMEM167A    1.000      4.250             0.647   4.250   
ENSG00000137720   C11orf1    1.000      4.250             0.295     nan   
ENSG00000153006  SREK1IP1    1.000      4.250            -0.588     nan   
ENSG00000131943  C19orf12    1.000      4.000             0.641     nan   
ENSG00000169989     TIGD4    1.000      4.000            -0.115     nan   
ENSG00000100220      RTCB    1.000      4.000            -0.128     nan   
ENSG00000128573     FOXP2    1.000      4.000            -0.264   4.000   
ENSG00000010219     DYRK4    1.000      3.750             0.487     nan   
ENSG00000154328     NEIL2    1.000      3.500             0.251   3.500   
ENSG00000109917      ZPR1    1.000      3.500             0.031     nan   
ENSG00000049245     VAMP3    1.000      3.500             0.011     nan   
ENSG00000164404      GDF9    1.000      3.250             0.491     nan   
ENSG00000186010   NDUFA13    1.000      3.00

### Temperature ###

In [20]:
stage_one_temperature = run_stage_one("temperature")
stage_one_temperature.selected

2020-09-13 01:17:56.260 | INFO     | yspecies.selection:fit:79 - ===== fitting models with seed 0 =====
2020-09-13 01:17:56.261 | INFO     | yspecies.selection:fit:80 - PARAMETERS:
{'bagging_fraction': 0.9219040738483888, 'boosting_type': 'gbdt', 'drop_rate': 0.14333380957397163, 'feature_fraction': 0.4690000754748763, 'lambda_l1': 0.4937008772491574, 'lambda_l2': 2.2888258490505713, 'learning_rate': 0.08533038187327897, 'max_depth': 3, 'max_leaves': 19, 'min_data_in_leaf': 4, 'objective': 'regression', 'metrics': ['l1', 'l2', 'huber'], 'verbose': -1, 'early_stopping_round': 10}
2020-09-13 01:17:56.287 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 0 | VALIDATION_SPECIES: ['Rattus_norvegicus', 'Suricata_suricatta']
Found `early_stopping_round` in params. Will use it instead of argument


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[95]	valid_0's l1: 0.37369	valid_0's l2: 0.281856	valid_0's huber: 0.127591


2020-09-13 01:17:57.967 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 1 | VALIDATION_SPECIES: ['Gorilla_gorilla', 'Cavia_porcellus']


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[39]	valid_0's l1: 1.14129	valid_0's l2: 2.16311	valid_0's huber: 0.716447


2020-09-13 01:17:59.455 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 2 | VALIDATION_SPECIES: ['Tupaia_belangeri', 'Mesocricetus_auratus']


...

Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[87]	valid_0's l1: 0.73849	valid_0's l2: 1.08005	valid_0's huber: 0.392066


2020-09-13 01:20:43.874 | INFO     | yspecies.selection:fit:83 - SEED: 9 | FOLD: 3 | VALIDATION_SPECIES: ['Cavia_porcellus', 'Mus_musculus']


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[33]	valid_0's l1: 1.09689	valid_0's l2: 2.00601	valid_0's huber: 0.646606


2020-09-13 01:20:58.013 | INFO     | yspecies.selection:transform:227 - Metrics: 
Metrics(R2=-0.033497055220625405, MAE=1.2636365478863747, MSE=3.7576705676926876, huber=0.8377271889400645)


symbol  repeats  mean_shap  mean_kendall_tau  shap_0  \
ENSG00000087460      GNAS    8.000     17.500             0.334  17.000   
ENSG00000092531    SNAP23    4.000      4.125             0.514     nan   
ENSG00000134717    BTF3L4    3.000      4.583             0.514     nan   
ENSG00000156467     UQCRB    3.000      4.333            -0.391   5.000   
ENSG00000127184     COX7C    3.000      4.333            -0.637     nan   
ENSG00000173890    GPR160    3.000      4.250             0.532     nan   
ENSG00000136942     RPL35    3.000      3.250            -0.666     nan   
ENSG00000176731      RBIS    2.000      5.125            -0.432     nan   
ENSG00000099341     PSMD8    2.000      4.125             0.433   4.500   
ENSG00000120656     TAF12    2.000      3.250             0.474     nan   
ENSG00000187840  EIF4EBP1    2.000      3.000             0.050   3.250   
ENSG00000126457     PRMT1    2.000      2.625             0.509     nan   
ENSG00000115204     MPV17    2.000      2.500            -0.618     nan   
ENSG00000018610   CXorf56    2.000      1.875            -0.310     nan   
ENSG00000105993    DNAJB6    1.000     11.500             0.317     nan   
ENSG00000149548    CCDC15    1.000      7.750            -0.165     nan   
ENSG00000198860    TSEN15    1.000      4.500             0.514     nan   
ENSG00000176909    MAMSTR    1.000      4.250             0.279     nan   
ENSG00000205323     SARNP    1.000      4.000            -0.193     nan   
ENSG00000204899      MZT1    1.000      3.750             0.569     nan   
ENSG00000100220      RTCB    1.000      3.750            -0.657     nan   
ENSG00000165119    HNRNPK    1.000      3.000             0.289     nan   
ENSG00000183625      CCR3    1.000      2.750             0.045     nan   
ENSG00000010219     DYRK4    1.000      2.750            -0.627     nan   
ENSG00000143575      HAX1    1.000      2.500            -0.470     nan   
ENSG00000122952     ZWINT    1.000      2.500            -0.486     nan   
ENSG00000146453    PNLDC1    1.000      2.500            -0.622     nan   
ENSG00000170264   FAM161A    1.000      2.250             0.595     nan   
ENSG00000132423      COQ3    1.000      2.250             0.537     nan   
ENSG00000198015    MRPL42    1.000      2.000             0.514     nan   
ENSG00000089053    ANAPC5    1.000      2.000            -0.635     nan   
ENSG00000215183      MSMP    1.000      1.750             0.656     nan   
ENSG00000105261     OVOL3    1.000      1.750             0.540     nan   
ENSG00000072840       EVC    1.000      1.500            -0.143     nan   
ENSG00000124091     GCNT7    1.000      1.500            -0.303     nan   
ENSG00000171735    CAMTA1    1.000      1.500            -0.471     nan   
ENSG00000095777     MYO3A    1.000      1.250            -0.440   1.250   

                 kendall_tau_0  shap_1  kendall_tau_1  shap_2  kendall_tau_2  \
ENSG00000087460          0.339  15.500          0.384  17.250          0.230   
ENSG00000092531            nan   4.250          0.480     nan            nan   
ENSG00000134717            nan     nan            nan     nan            nan   
ENSG00000156467         -0.359     nan            nan     nan            nan   
ENSG00000127184            nan     nan            nan   4.500         -0.652   
ENSG00000173890            nan     nan            nan     nan            nan   
ENSG00000136942            nan     nan            nan   4.750         -0.719   
ENSG00000176731            nan     nan            nan     nan            nan   
ENSG00000099341          0.355     nan            nan     nan            nan   
ENSG00000120656            nan     nan            nan     nan            nan   
ENSG00000187840          0.112     nan            nan     nan            nan   
ENSG00000126457            nan     nan            nan     nan            nan   
ENSG00000115204            nan     nan            nan   3.250         -0.595   
ENSG00000018610            nan     nan          

### Gestation ###

In [21]:
stage_one_gestation = run_stage_one("gestation_days")
stage_one_gestation.selected

2020-09-13 01:20:58.223 | INFO     | yspecies.selection:fit:79 - ===== fitting models with seed 0 =====
2020-09-13 01:20:58.224 | INFO     | yspecies.selection:fit:80 - PARAMETERS:
{'bagging_fraction': 0.9550809144864345, 'boosting_type': 'gbdt', 'drop_rate': 0.1520029135951902, 'feature_fraction': 0.39359679175101914, 'lambda_l1': 2.2144413347584315, 'lambda_l2': 2.012506929626787, 'learning_rate': 0.0890025107137548, 'max_depth': 3, 'max_leaves': 18, 'min_data_in_leaf': 5, 'objective': 'regression', 'metrics': ['l1', 'l2', 'huber'], 'verbose': -1, 'early_stopping_round': 10}
2020-09-13 01:20:58.255 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 0 | VALIDATION_SPECIES: ['Homo_sapiens', 'Pan_paniscus']
Found `early_stopping_round` in params. Will use it instead of argument


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[223]	valid_0's l1: 39.8955	valid_0's l2: 4547.51	valid_0's huber: 35.5331


2020-09-13 01:21:00.977 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 1 | VALIDATION_SPECIES: ['Capra_hircus', 'Cavia_porcellus']


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[103]	valid_0's l1: 14.7475	valid_0's l2: 669.363	valid_0's huber: 12.8995


2020-09-13 01:21:03.014 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 2 | VALIDATION_SPECIES: ['Cavia_aperea', 'Microcebus_murinus']


...

Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[192]	valid_0's l1: 15.396	valid_0's l2: 797.497	valid_0's huber: 13.482


2020-09-13 01:26:06.336 | INFO     | yspecies.selection:fit:83 - SEED: 9 | FOLD: 3 | VALIDATION_SPECIES: ['Homo_sapiens', 'Ailuropoda_melanoleuca']


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[74]	valid_0's l1: 34.7252	valid_0's l2: 3528.39	valid_0's huber: 30.8726


2020-09-13 01:26:29.308 | INFO     | yspecies.selection:transform:227 - Metrics: 
Metrics(R2=0.7206068064267933, MAE=25.499474903570643, MSE=2180.783212310389, huber=22.571443975436978)


symbol  repeats  mean_shap  mean_kendall_tau  shap_0  \
ENSG00000006282   SPATA20   10.000      7.400             0.660   5.500   
ENSG00000066923     STAG3   10.000      6.500             0.424   6.250   
ENSG00000171121    KCNMB3   10.000      5.900             0.623   5.500   
ENSG00000172531    PPP1CA    9.000      5.250            -0.755   8.000   
ENSG00000105672      ETV2    9.000      4.083             0.681   4.750   
ENSG00000188747     NOXA1    9.000      3.944             0.651   3.750   
ENSG00000010219     DYRK4    8.000     11.219             0.474  13.250   
ENSG00000163584   RPL22L1    7.000      4.214            -0.586   3.500   
ENSG00000165568    AKR1E2    7.000      4.071            -0.519   2.250   
ENSG00000101190     TCFL5    7.000      2.929             0.650   3.000   
ENSG00000154328     NEIL2    7.000      2.857             0.584     nan   
ENSG00000132436    FIGNL1    6.000      3.417             0.445   2.500   
ENSG00000013288    MAN2B2    6.000      2.958            -0.362   4.750   
ENSG00000157343    ARMC12    6.000      1.917             0.642   2.750   
ENSG00000137161     CNPY3    5.000      8.700            -0.144     nan   
ENSG00000164304     CAGE1    5.000      4.150            -0.722     nan   
ENSG00000164362      TERT    5.000      2.750            -0.628     nan   
ENSG00000162959     MEMO1    4.000      3.562            -0.257   6.000   
ENSG00000166562    SEC11C    4.000      3.188            -0.072   5.000   
ENSG00000060762      MPC1    4.000      2.938            -0.259     nan   
ENSG00000120675   DNAJC15    4.000      2.562            -0.669     nan   
ENSG00000167701       GPT    4.000      2.438            -0.487     nan   
ENSG00000168569   TMEM223    3.000      3.000            -0.512     nan   
ENSG00000144451    SPAG16    3.000      2.750             0.460     nan   
ENSG00000143578   CREB3L4    3.000      1.333             0.633     nan   
ENSG00000196419     XRCC6    2.000      2.625             0.481     nan   
ENSG00000117697      NSL1    2.000      2.375             0.673     nan   
ENSG00000127952    STYXL1    2.000      2.250             0.520     nan   
ENSG00000205323     SARNP    2.000      2.250            -0.238     nan   
ENSG00000154485     MMP21    2.000      2.125             0.409     nan   
ENSG00000053372     MRTO4    2.000      2.125            -0.384   2.500   
ENSG00000162624      LHX8    2.000      2.000            -0.428   2.250   
ENSG00000269058     CALR3    2.000      2.000            -0.529     nan   
ENSG00000214941    ZSWIM7    2.000      1.875             0.672     nan   
ENSG00000142937      RPS8    2.000      1.375             0.610     nan   
ENSG00000079246     XRCC5    2.000      1.250             0.436     nan   
ENSG00000131504    DIAPH1    1.000     11.250            -0.166     nan   
ENSG00000132793     LPIN3    1.000      5.500             0.495     nan   
ENSG00000137815      RTF1    1.000      3.250             0.035     nan   
ENSG00000114405   C3orf14    1.000      3.000            -0.462     nan   
ENSG00000124172   ATP5F1E    1.000      3.000            -0.475     nan   
ENSG00000173769    TOPAZ1    1.000      2.750            -0.523     nan   
ENSG00000183864      TOB2    1.000      2.500             0.513     nan   
ENSG00000143443   C1orf56    1.000      2.250             0.611     nan   
ENSG00000106682     EIF4H    1.000      2.250             0.134     nan   
ENSG00000104267       CA2    1.000      2.250             0.028     nan   
ENSG00000143753     DEGS1    1.000      2.250            -0.322     nan   
ENSG00000278023      RDM1    1.000      2.250            -0.430     nan   
ENSG00000023191      RNH1    1.000      2.250            -0.489   2.250   
ENSG00000175121     WFDC5    1.000      2.250            -0.517   2.250   
ENSG00000115361     ACADL    1.000      2.250            -0.585     nan   
ENSG00000010610       CD4    1.000      1.750             0.593     nan   
ENSG00000176261   ZBTB8OS    1.000      1.75

## Intersect first stages ##

In [22]:
genes = FeatureSummary.concat(stage_one, 2)
genes.shape

(142,)

In [71]:
stage_one["lifespan"].selected.columns

Index(['symbol', 'repeats', 'mean_shap', 'mean_kendall_tau', 'shap_0',
       'kendall_tau_0', 'shap_1', 'kendall_tau_1', 'shap_2', 'kendall_tau_2',
       'shap_3', 'kendall_tau_3', 'shap_4', 'kendall_tau_4', 'shap_5',
       'kendall_tau_5', 'shap_6', 'kendall_tau_6', 'shap_7', 'kendall_tau_7',
       'shap_8', 'kendall_tau_8', 'shap_9', 'kendall_tau_9'],
      dtype='object')

In [81]:
df = genes.to_frame()
for key, stage in stage_one.items():
    df = df.join(stage.selected["mean_kendall_tau"], how="left", rsuffix="_"+key)
for key, stage in stage_one.items():
    df = df.join(stage.selected["mean_shap"], how="left", rsuffix="_"+key)
df

symbol  mean_kendall_tau  mean_kendall_tau_mass_kg  \
ENSG00000010219     DYRK4             0.263                     0.212   
ENSG00000204498   NFKBIL1            -0.141                    -0.193   
ENSG00000066923     STAG3             0.438                     0.154   
ENSG00000185880    TRIM69             0.140                       nan   
ENSG00000105672      ETV2             0.730                       nan   
ENSG00000167515  TRAPPC2L            -0.168                       nan   
ENSG00000171121    KCNMB3             0.667                       nan   
ENSG00000132436    FIGNL1             0.544                       nan   
ENSG00000157343    ARMC12             0.629                       nan   
ENSG00000170835       CEL             0.694                       nan   
ENSG00000188747     NOXA1             0.692                       nan   
ENSG00000106554    CHCHD3            -0.381                       nan   
ENSG00000164362      TERT            -0.444                       nan   
ENSG00000129187      DCTD             0.624                       nan   
ENSG00000144451    SPAG16             0.475                       nan   
ENSG00000172531    PPP1CA            -0.712                       nan   
ENSG00000013288    MAN2B2            -0.301                       nan   
ENSG00000160948     VPS28            -0.329                       nan   
ENSG00000023191      RNH1            -0.319                       nan   
ENSG00000165555   NOXRED1             0.799                       nan   
ENSG00000108384    RAD51C             0.388                     0.173   
ENSG00000142002      DPP9            -0.703                       nan   
ENSG00000152705  CATSPER3             0.684                       nan   
ENSG00000132464      ENAM             0.491                       nan   
ENSG00000066926      FECH            -0.421                       nan   
ENSG00000136436  CALCOCO2             0.684                       nan   
ENSG00000184983    NDUFA6            -0.638                       nan   
ENSG00000165501      LRR1             0.658                       nan   
ENSG00000164879       CA3            -0.435                       nan   
ENSG00000182612   TSPAN10             0.453                       nan   
ENSG00000137343     ATAT1            -0.403                       nan   
ENSG00000142541    RPL13A            -0.185                       nan   
ENSG00000213719     CLIC1            -0.252                    -0.091   
ENSG00000102265     TIMP1             0.589                     0.031   
ENSG00000108786   HSD17B1             0.651                       nan   
ENSG00000140398     NEIL1             0.481                       nan   
ENSG00000144214      LYG1               nan                     0.408   
ENSG00000124172   ATP5F1E            -0.280                    -0.299   
ENSG00000054277      OPN3               nan                     0.150   
ENSG00000126062   TMEM115               nan                     0.005   
ENSG00000107020    PLGRKT               nan                     0.015   
ENSG00000270647     TAF15               nan                     0.043   
ENSG00000152214      RIT2               nan                     0.065   
ENSG00000164304     CAGE1               nan                    -0.191   
ENSG00000117151      CTBS               nan                    -0.268   
ENSG00000101104   PABPC1L               nan                     0.308   
ENSG00000122034     GTF3A               nan                       nan   
ENSG00000196419     XRCC6               nan                       nan   
ENSG00000163528    CHCHD4               nan                       nan   
ENSG00000167272      POP5               nan                       nan   
ENSG00000122952     ZWINT               nan                       nan   
ENSG00000069869     NEDD4               nan                       nan   
ENSG00000168300    PCMTD1               nan                       nan   
ENSG00000006282   SPATA20               nan                       nan   
ENSG

In [23]:
genes.to_list()

['DYRK4',
 'NFKBIL1',
 'STAG3',
 'TRIM69',
 'ETV2',
 'TRAPPC2L',
 'KCNMB3',
 'FIGNL1',
 'ARMC12',
 'CEL',
 'NOXA1',
 'CHCHD3',
 'TERT',
 'DCTD',
 'SPAG16',
 'PPP1CA',
 'MAN2B2',
 'VPS28',
 'RNH1',
 'NOXRED1',
 'RAD51C',
 'DPP9',
 'CATSPER3',
 'ENAM',
 'FECH',
 'CALCOCO2',
 'NDUFA6',
 'LRR1',
 'CA3',
 'TSPAN10',
 'ATAT1',
 'RPL13A',
 'CLIC1',
 'TIMP1',
 'HSD17B1',
 'NEIL1',
 'LYG1',
 'ATP5F1E',
 'OPN3',
 'TMEM115',
 'PLGRKT',
 'TAF15',
 'RIT2',
 'CAGE1',
 'CTBS',
 'PABPC1L',
 'GTF3A',
 'XRCC6',
 'CHCHD4',
 'POP5',
 'ZWINT',
 'NEDD4',
 'PCMTD1',
 'SPATA20',
 'NEIL2',
 'EIF3K',
 'YES1',
 'LGALS4',
 'SFR1',
 'MRPL43',
 'TSPAN17',
 'AKR7L',
 'TCFL5',
 'CETN1',
 'GPAT3',
 'ELOC',
 'ATP5PD',
 'CAPN3',
 'MOSPD1',
 'PRSS53',
 'ZC3H15',
 'EMC9',
 'MRPL45',
 'PARP4',
 'PKN3',
 'YIPF6',
 'TSPAN31',
 'YWHAQ',
 'CALR3',
 'DTYMK',
 'PSMG3',
 'C12orf73',
 'STRC',
 'MPEG1',
 'RPL22L1',
 'PLXDC2',
 'ERMAP',
 'RPS17',
 'LYPLA1',
 'TESC',
 'DMAC1',
 'BRCA2',
 'AKR1E2',
 'RPL28',
 'NUCKS1',
 'UPP2',
 'MSRA',
 'STYXL1',
 'TMEM258',
 'UQCRB',
 'APRT',
 'CENPT',
 'MLYCD',
 'NDUFA4',
 'NDUFAF2',
 'RBFA',
 'CCR3',
 'USB1',
 'ZDHHC12',
 'C6orf89',
 'VMO1',
 'SLC25A43',
 'CHRNE',
 'GNAS',
 'SNAP23',
 'BTF3L4',
 'COX7C',
 'GPR160',
 'RPL35',
 'RBIS',
 'PSMD8',
 'TAF12',
 'EIF4EBP1',
 'PRMT1',
 'MPV17',
 'CXorf56',
 'CNPY3',
 'MEMO1',
 'SEC11C',
 'MPC1',
 'DNAJC15',
 'GPT',
 'TMEM223',
 'CREB3L4',
 'NSL1',
 'SARNP',
 'MMP21',
 'MRTO4',
 'LHX8',
 'ZSWIM7',
 'RPS8',
 'XRCC5']

## Second stage selection ##

In [43]:
lifespan_selection = selections["lifespan"]

In [44]:
initial_data = lifespan_selection[0] #.by_genes()

In [53]:
genes.to_csv(locations.interim.stage_one / "results_concatenated.tsv", sep="\t", index_label="reference_gene")

In [54]:
stage_two_data = initial_data.by_genes.collect(lambda gs: gs.loc[genes.index.to_list()])
stage_two_data.name = "input"
stage_two_data

<table border='2'><caption>input<caption><tr><th>expressions</th><th>genes</th><th>species</th><th>samples</th><th>Genes Metadata</th><th>Species Metadata</th></tr><tr><td>(408, 142)</td><td>(142, 37)</td><td>38</td><td>408</td><td>(142, 2)</td><td>(38, 18)</td></tr></table>

In [55]:
stage_two_data.write(locations.interim.stage_two)

written input dataset content to ../data/interim/stage_2/input


PosixPath('../data/interim/stage_2/input')

In [56]:
stage_two_selection = (stage_two_data,lifespan_selection[1])

# Check untuned performance #

In [58]:
summary_stage_one_plot_path = locations.output.plots / "stage_one_summary_lifespan.svg"
summary_stage_one = stage_one["lifespan"]
stage_one_figure = summary_stage_one.plot(max_display=50, plot_size=0.5, save = summary_stage_one_plot_path)
stage_one_figure

### Saving stage 1 results ###

In [31]:
for k, v in stage_one.items():
    res = v.select_repeated(2)
    res.to_csv(locations.output.stage_one / f"{k}_selected.tsv", sep="\t", index_label="reference_gene")

In [32]:
stage_one["lifespan"].select_repeated(2)

symbol  repeats  mean_shap  mean_kendall_tau  shap_0  \
ENSG00000010219     DYRK4   10.000      8.375             0.263   8.250   
ENSG00000204498   NFKBIL1   10.000      7.350            -0.141   5.500   
ENSG00000066923     STAG3   10.000      5.525             0.438   5.250   
ENSG00000185880    TRIM69   10.000      5.200             0.140   5.250   
ENSG00000105672      ETV2   10.000      3.550             0.730   2.750   
ENSG00000167515  TRAPPC2L    9.000      6.056            -0.168     nan   
ENSG00000171121    KCNMB3    9.000      4.056             0.667   5.250   
ENSG00000132436    FIGNL1    9.000      3.722             0.544   4.250   
ENSG00000157343    ARMC12    9.000      2.639             0.629   3.000   
ENSG00000170835       CEL    8.000      3.219             0.694   2.500   
ENSG00000188747     NOXA1    8.000      2.656             0.692   1.250   
ENSG00000106554    CHCHD3    7.000      2.929            -0.381     nan   
ENSG00000164362      TERT    7.000      2.893            -0.444   2.250   
ENSG00000129187      DCTD    7.000      1.607             0.624     nan   
ENSG00000144451    SPAG16    6.000      3.625             0.475     nan   
ENSG00000172531    PPP1CA    5.000      2.700            -0.712   2.000   
ENSG00000013288    MAN2B2    5.000      2.650            -0.301     nan   
ENSG00000160948     VPS28    5.000      2.250            -0.329   3.500   
ENSG00000023191      RNH1    4.000      4.000            -0.319     nan   
ENSG00000165555   NOXRED1    4.000      3.938             0.799     nan   
ENSG00000108384    RAD51C    4.000      3.438             0.388     nan   
ENSG00000142002      DPP9    4.000      2.500            -0.703   2.250   
ENSG00000152705  CATSPER3    4.000      2.062             0.684     nan   
ENSG00000132464      ENAM    4.000      2.000             0.491   2.000   
ENSG00000066926      FECH    4.000      1.875            -0.421   1.250   
ENSG00000136436  CALCOCO2    4.000      1.500             0.684     nan   
ENSG00000184983    NDUFA6    3.000      2.750            -0.638     nan   
ENSG00000165501      LRR1    3.000      2.250             0.658     nan   
ENSG00000164879       CA3    3.000      1.083            -0.435     nan   
ENSG00000182612   TSPAN10    2.000      3.875             0.453     nan   
ENSG00000137343     ATAT1    2.000      2.875            -0.403     nan   
ENSG00000142541    RPL13A    2.000      2.625            -0.185   2.750   
ENSG00000213719     CLIC1    2.000      2.500            -0.252     nan   
ENSG00000102265     TIMP1    2.000      2.000             0.589   1.500   
ENSG00000108786   HSD17B1    2.000      1.875             0.651   1.750   
ENSG00000140398     NEIL1    2.000      1.750             0.481     nan   

                 kendall_tau_0  shap_1  kendall_tau_1  shap_2  kendall_tau_2  \
ENSG00000010219          0.261   8.000          0.249   8.000          0.211   
ENSG00000204498         -0.057   8.750         -0.030   7.250         -0.114   
ENSG00000066923          0.378   4.000          0.397   8.500          0.447   
ENSG00000185880          0.073   4.500          0.313   3.750          0.119   
ENSG00000105672          0.752   3.250          0.769   2.750          0.729   
ENSG00000167515            nan   4.750         -0.205   4.750         -0.137   
ENSG00000171121          0.725   3.750          0.660     nan            nan   
ENSG00000132436          0.475   3.000          0.563     nan            nan   
ENSG00000157343          0.625   2.000          0.632     nan            nan   
ENSG00000170835          0.738   3.500          0.748     nan            nan   
ENSG00000188747          0.718   2.250          0.699   1.500          0.761   
ENSG00000106554            nan     nan            nan   4.500         -0.362   
ENSG00000164362         -0.360   2.250         -0.411     nan            nan   
ENSG00000129187            nan   1.750          0.629   1.500          0.631   
ENSG00000144451            nan   2.500     

In [33]:
result_untuned = pipelines["lifespan"].fit_transform(stage_two_selection)
result_untuned.selected

2020-09-13 01:26:36.178 | INFO     | yspecies.selection:fit:79 - ===== fitting models with seed 0 =====
2020-09-13 01:26:36.179 | INFO     | yspecies.selection:fit:80 - PARAMETERS:
{'bagging_fraction': 0.9223944053685549, 'boosting_type': 'gbdt', 'drop_rate': 0.29847846764282016, 'feature_fraction': 0.30501714460224083, 'lambda_l1': 0.21894440516534, 'lambda_l2': 1.3848191603958375, 'learning_rate': 0.08210966706622723, 'max_depth': 3, 'max_leaves': 17, 'min_data_in_leaf': 8, 'objective': 'regression', 'metrics': ['l1', 'l2', 'huber'], 'verbose': -1, 'early_stopping_round': 10, 'seed': 9}
2020-09-13 01:26:36.183 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 0 | VALIDATION_SPECIES: ['Gorilla_gorilla', 'Pan_paniscus']
Found `early_stopping_round` in params. Will use it instead of argument


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[187]	valid_0's l1: 7.5055	valid_0's l2: 169.317	valid_0's huber: 6.4125


2020-09-13 01:26:36.404 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 1 | VALIDATION_SPECIES: ['Heterocephalus_glaber', 'Capra_hircus']


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[134]	valid_0's l1: 3.2507	valid_0's l2: 45.5218	valid_0's huber: 2.59336


2020-09-13 01:26:36.545 | INFO     | yspecies.selection:fit:83 - SEED: 0 | FOLD: 2 | VALIDATION_SPECIES: ['Bos_taurus', 'Otolemur_garnettii']


...

Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[88]	valid_0's l1: 3.36084	valid_0's l2: 26.4881	valid_0's huber: 2.66332


2020-09-13 01:28:54.172 | INFO     | yspecies.selection:fit:83 - SEED: 9 | FOLD: 3 | VALIDATION_SPECIES: ['Gorilla_gorilla', 'Microcebus_murinus']


Training until validation scores don't improve for 10 rounds
Training until validation scores don't improve for 10 rounds
Early stopping, best iteration is:
[107]	valid_0's l1: 4.3892	valid_0's l2: 61.4984	valid_0's huber: 3.60432


2020-09-13 01:29:06.955 | INFO     | yspecies.selection:transform:227 - Metrics: 
Metrics(R2=0.9294056800176123, MAE=4.175251441163073, MSE=54.00858654469263, huber=3.4046294070142604)


symbol  repeats  mean_shap  mean_kendall_tau  shap_0  \
ENSG00000204498   NFKBIL1   10.000     13.975            -0.496  17.250   
ENSG00000010219     DYRK4   10.000     13.600             0.475  12.000   
ENSG00000167515  TRAPPC2L   10.000     12.650            -0.383  12.500   
ENSG00000142002      DPP9   10.000     11.825            -0.800  14.000   
ENSG00000023191      RNH1   10.000     11.650            -0.552  16.000   
ENSG00000165501      LRR1   10.000     11.575             0.703  19.500   
ENSG00000160948     VPS28   10.000     11.225            -0.538  11.250   
ENSG00000170835       CEL   10.000     10.775             0.728   6.250   
ENSG00000137343     ATAT1   10.000      9.850            -0.578   9.000   
ENSG00000184983    NDUFA6   10.000      9.700            -0.607   8.500   
ENSG00000164362      TERT   10.000      8.800            -0.559  12.250   
ENSG00000066926      FECH   10.000      8.775            -0.538   7.250   
ENSG00000105672      ETV2   10.000      8.700             0.700  17.000   
ENSG00000132436    FIGNL1   10.000      8.700             0.550   9.500   
ENSG00000165555   NOXRED1   10.000      8.625             0.805   9.750   
ENSG00000066923     STAG3   10.000      8.600             0.484  12.250   
ENSG00000185880    TRIM69   10.000      8.500            -0.050  10.500   
ENSG00000136436  CALCOCO2   10.000      7.950             0.748   7.750   
ENSG00000013288    MAN2B2   10.000      7.625            -0.654   7.250   
ENSG00000172531    PPP1CA   10.000      7.225            -0.765   9.000   
ENSG00000164304     CAGE1   10.000      6.975            -0.728  13.750   
ENSG00000122952     ZWINT   10.000      6.950            -0.633  11.750   
ENSG00000213719     CLIC1   10.000      6.875            -0.505  11.250   
ENSG00000092529     CAPN3   10.000      6.800             0.561  11.500   
ENSG00000198663   C6orf89   10.000      6.625            -0.745   6.250   
ENSG00000142937      RPS8   10.000      6.475             0.624  11.500   
ENSG00000140398     NEIL1   10.000      6.400             0.655   8.250   
ENSG00000120992    LYPLA1   10.000      6.350            -0.590  10.750   
ENSG00000162959     MEMO1   10.000      6.275            -0.613   9.000   
ENSG00000142541    RPL13A   10.000      5.950            -0.084  10.000   
ENSG00000127952    STYXL1   10.000      5.900             0.560   8.250   
ENSG00000103150     MLYCD   10.000      5.900            -0.211  10.000   
ENSG00000106554    CHCHD3   10.000      5.825            -0.575   8.250   
ENSG00000102265     TIMP1   10.000      5.700             0.593  12.000   
ENSG00000152705  CATSPER3   10.000      5.675             0.691   6.500   
ENSG00000188747     NOXA1   10.000      5.375             0.699   4.750   
ENSG00000117151      CTBS   10.000      4.750            -0.668   5.000   
ENSG00000157343    ARMC12   10.000      4.500             0.612   8.750   
ENSG00000164879       CA3   10.000      4.075            -0.462   4.500   
ENSG00000129187      DCTD   10.000      3.550             0.658   5.250   
ENSG00000175806      MSRA    9.000      8.000            -0.299  18.000   
ENSG00000211454     AKR7L    9.000      7.639             0.009   7.500   
ENSG00000144451    SPAG16    9.000      7.583             0.494   7.500   
ENSG00000101546      RBFA    9.000      7.556             0.107  12.500   
ENSG00000138678     GPAT3    9.000      7.361             0.746   9.000   
ENSG00000053372     MRTO4    9.000      7.333            -0.704   9.250   
ENSG00000127184     COX7C    9.000      5.833             0.614   7.250   
ENSG00000120675   DNAJC15    9.000      5.694            -0.621   6.000   
ENSG00000102901     CENPT    9.000      5.611            -0.295   6.750   
ENSG00000205323     SARNP    9.000      5.417            -0.469   6.500   
ENSG00000171121    KCNMB3    9.000      5.306             0.654   5.500   
ENSG00000136942     RPL35    9.000      5.167            -0.576   8.750   
ENSG00000269058     CALR3    9.000      5.13

In [41]:
summary_stage_two_untuned_plot_path = locations.output.dir / "plots" / "stage_two_untuned_summary_lifespan.svg"
summary_stage_two_untuned = result_untuned.plot(max_display=50, plot_size=0.5, save = summary_stage_two_untuned_plot_path)
summary_stage_two_untuned

### Comparing metrics ###

In [ ]:
stage_one["lifespan"].metrics_average

In [ ]:
stage_one["lifespan"].symbols_repeated(6).values

In [ ]:
stage_one["lifespan"].symbols_repeated(2).index

In [ ]:
stage_one["lifespan"].validation_metrics.mean(axis=0)

In [ ]:
(stage_one["lifespan"].symbols_repeated(2).shape, result_untuned.symbols_repeated(2).shape)

In [ ]:
result_untuned.metrics_average

In [ ]:
result_untuned.validation_metrics["R^2"].mean()

In [ ]:
#result_untuned.metrics_average

In [ ]:
### Train stage 2 model with same parameters

In [ ]:
locations.output.dir / "stage_one_lifespan.csv"